In [6]:
%%time

import pandas as pd
import numpy
import os
import tarfile
import dask
from dask.distributed import Client, progress
client = Client(threads_per_worker=2, n_workers=6)

def genotype_compare(geno_a, geno_b):
  (a1, a2) = geno_a.split("|")
  (b1, b2) = geno_b.split("|")

  if a1 == b1 and a2 == b2:
    return 1
  elif a1 == b2 and a2 == b1:
    return 1
  elif a1 == b1 or a2 == b2:
    return .5
  else:
    return 0

def test_genotype_compare():
    assert genotype_compare("1|1", "1|1") == 1
    assert genotype_compare("0|0", "0|0") == 1
    assert genotype_compare("1|0", "1|0") == 1
    assert genotype_compare("0|1", "0|1") == 1
    assert genotype_compare("1|0", "0|1") == 1

    assert genotype_compare("1|1", "0|1") == 0.5
    assert genotype_compare("0|0", "0|1") == 0.5
    assert genotype_compare("1|1", "1|0") == 0.5
    assert genotype_compare("0|0", "1|0") == 0.5

    assert genotype_compare("1|1", "0|0") == 0.0
    assert genotype_compare("0|0", "1|1") == 0.0

test_genotype_compare()

def make_matrix(row, samples):
  array = numpy.zeros(shape=[len(samples), len(samples)])
  for j, sample_a in enumerate(samples):
    for k, sample_b in enumerate(samples):
      array[j,k] = genotype_compare(row[sample_a], row[sample_b])
  return array

def export_matrix(vcf_file, skip_rows):
    # todo: handle skiprows?

    vcf_df = pd.read_csv(vcf_file, sep="\t", skiprows=skip_rows, dtype='string')
    samples = list(vcf_df.columns)[9:]
    vcf_df['matrix'] = vcf_df.apply(lambda row: make_matrix(row, samples), axis=1)

    vcf_file_base = '.'.join(os.path.basename(vcf_file).split('.')[:-2])

    tar_file_name = f"{vcf_file_base}.row_matrices.tar.gz"

    # create tar file
    with tarfile.open(tar_file_name, "w:gz") as tar:
        for row in range(0,vcf_df.shape[0]):
          row_df = pd.DataFrame(vcf_df.iloc[row]['matrix'], columns=samples, index=samples)
          id = vcf_df.iloc[row]['ID']
          filename = f"{vcf_file_base}.{id}.matrix.tsv"
          row_df.to_csv(filename, sep="\t")
          tar.add(filename)
          os.remove(filename)

    tar.close()

    return tar_file_name

# This is just a dummy function for dask reasons
def join(a):
    print(a)

def generate_matrices():
    phenotypes = ["max_height_cm", "max_growth_cm_gdd"]
    pvalues = ["p0001", "p0005", "p001"]

    delayed_results = []

    for phenotype in phenotypes:
        for pvalue in pvalues:
            delayed_results.append(dask.delayed(export_matrix)(f"../vcf/sorghum.filtered.season4.season6.{phenotype}_{pvalue}.vcf.gz", skip_rows=83))
            delayed_results.append(dask.delayed(export_matrix)(f"../vcf/sorghum.filtered.season4.season6.{phenotype}_{pvalue}_qtl.vcf.gz", skip_rows=84))

    x = dask.delayed(join)(delayed_results)
    x.compute()

generate_matrices()

/Users/kschaper/Documents/Monarch/sorghum_data/venv/lib/python3.10/site-packages/distributed/node.py:183: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 52137 instead
  warnings.warn(
2022-10-12 22:08:42,199 - distributed.worker - WARNING - Mismatched versions found

+---------+---------------------------------------------+-----------+---------+
| Package | Worker-a293a8c6-0272-43cf-90d9-43f5801c72db | Scheduler | Workers |
+---------+---------------------------------------------+-----------+---------+
| tornado | 6.1                                         | 6.2       | 6.1     |
+---------+---------------------------------------------+-----------+---------+
2022-10-12 22:08:42,200 - distributed.worker - WARNING - Mismatched versions found

+---------+---------------------------------------------+-----------+---------+
| Package | Worker-3a6c0e61-5679-4cd9-ba44-8cc10567dbfb | Scheduler | Workers |
+---------+------

KilledWorker: Attempted to run task export_matrix-4d916955-f2b5-4bcb-b6df-927c4443e7a9 on 3 different workers, but all those workers died while running it. The last worker that attempt to run the task was tcp://127.0.0.1:55402. Inspecting worker logs is often a good next step to diagnose what went wrong. For more information see https://distributed.dask.org/en/stable/killed.html.

2022-10-13 13:05:47,373 - distributed.worker - WARNING - Mismatched versions found

+---------+---------------------------------------------+-----------+---------+
| Package | Worker-1765f3f8-2271-48b0-9578-27b060e60199 | Scheduler | Workers |
+---------+---------------------------------------------+-----------+---------+
| tornado | 6.1                                         | 6.2       | 6.1     |
+---------+---------------------------------------------+-----------+---------+
